In [1]:
import pandas as pd
import numpy as np
import pulp

In [2]:
df_orders = pd.read_csv('./new_orders/orders.csv').reset_index(drop=True)

In [15]:
import pandas as pd
import pulp
from typing import Dict, Tuple, Optional
from dataclasses import dataclass

@dataclass
class OptimizacionResultado:
    """Clase para almacenar los resultados de la optimización"""
    plan_produccion: pd.DataFrame
    resumen_maquinas: pd.DataFrame
    utilizacion_capacidad: pd.DataFrame
    resumen_prioridades: pd.DataFrame
    resumen_productos: pd.DataFrame
    tiempo_total: float
    status: str

def procesar_ordenes(csv_data) -> Dict:
    """
    Procesa los datos del CSV y agrupa las órdenes por producto y prioridad
    """
    if isinstance(csv_data, str):
        df = pd.read_csv(csv_data)
    else:
        df = pd.DataFrame(csv_data)
    
    grouped = df.groupby(['product', 'priority'])['quantity'].sum().reset_index()
    
    demanda = {'A': {}, 'B': {}}
    for _, row in grouped.iterrows():
        producto = row['product']
        prioridad = int(row['priority'])
        cantidad = row['quantity']
        demanda[producto][prioridad] = cantidad
    
    return demanda

def optimizar_produccion(demanda_productos) -> OptimizacionResultado:
    """
    Optimiza la producción con balance de carga mejorado
    """
    prob = pulp.LpProblem("Optimizacion_Produccion", pulp.LpMinimize)
    
    # Parámetros
    maquinas_flexibles = ['M1', 'M2']
    maquinas_dedicadas = ['M3', 'M4']
    productos = ['A', 'B']
    prioridades = [1, 2, 3]
    
    # Tasas de producción (piezas por hora)
    tasa_produccion = {
        'M1': {'A': 144, 'B': 121},
        'M2': {'A': 144, 'B': 121},
        'M3': {'B': 105},
        'M4': {'B': 105}
    }
    
    tiempo_prod = {
        m: {p: 1/tasa_produccion[m][p] for p in tasa_produccion[m]}
        for m in tasa_produccion
    }
    
    # Variables de decisión
    x = pulp.LpVariable.dicts("produccion",
                             ((m, p, pr) for m in maquinas_flexibles + maquinas_dedicadas 
                              for p in productos if (m in maquinas_flexibles) or 
                              (m in maquinas_dedicadas and p == 'B')
                              for pr in prioridades),
                             lowBound=0,
                             cat='Integer')
    
    # Variables para el tiempo máximo y mínimo de utilización
    max_tiempo = pulp.LpVariable("max_tiempo", lowBound=0)
    min_tiempo = pulp.LpVariable("min_tiempo", lowBound=0)
    
    # Función objetivo: Minimizar el tiempo máximo y la diferencia entre máximo y mínimo
    prob += max_tiempo + (max_tiempo - min_tiempo)
    
    # Restricciones de demanda
    for p in productos:
        for pr in prioridades:
            if p == 'A':
                prob += pulp.lpSum(x[m,p,pr] for m in maquinas_flexibles) == demanda_productos[p][pr]
            else:
                prob += pulp.lpSum(x[m,p,pr] for m in maquinas_flexibles + maquinas_dedicadas) == demanda_productos[p][pr]
    
    # Restricciones de tiempo por máquina y balance
    for m in maquinas_flexibles + maquinas_dedicadas:
        tiempo_maquina = pulp.lpSum(x[m,p,pr] * tiempo_prod[m][p]
                                   for p in productos if (m in maquinas_flexibles) or 
                                   (m in maquinas_dedicadas and p == 'B')
                                   for pr in prioridades)
        
        # El tiempo de cada máquina debe ser menor que el máximo
        prob += tiempo_maquina <= max_tiempo
        
        # El tiempo de cada máquina debe ser mayor que el mínimo
        prob += tiempo_maquina >= min_tiempo
        
        # Límite de 8 horas por turno
        prob += tiempo_maquina <= 8
    
    # Restricciones adicionales para balance de carga
    # Asegurar uso mínimo de cada máquina (al menos 20% de su capacidad si hay demanda suficiente)
    min_utilizacion = 0.2
    for m in maquinas_flexibles + maquinas_dedicadas:
        prob += pulp.lpSum(x[m,p,pr] * tiempo_prod[m][p]
                          for p in productos if (m in maquinas_flexibles) or 
                          (m in maquinas_dedicadas and p == 'B')
                          for pr in prioridades) >= min_utilizacion * 8
    
    # Priorizar producción de alta prioridad en máquinas más rápidas
    for m in maquinas_flexibles:
        for p in productos:
            if p in tasa_produccion[m]:
                # Alta prioridad debe ser al menos 40% de la producción si hay demanda suficiente
                prob += x[m,p,1] >= 0.4 * pulp.lpSum(x[m,p,pr] for pr in prioridades)
    
    # Resolver
    status = prob.solve()
    status_msg = pulp.LpStatus[status]
    
    if status != 1:
        raise ValueError(f"No se encontró solución factible. Status: {status_msg}")
    
    # Crear DataFrame con resultados
    resultados = []
    for m in maquinas_flexibles + maquinas_dedicadas:
        for p in productos:
            if (m in maquinas_flexibles) or (m in maquinas_dedicadas and p == 'B'):
                for pr in prioridades:
                    if x[m,p,pr].value() > 0:
                        tiempo_total = x[m,p,pr].value() * tiempo_prod[m][p]
                        resultados.append({
                            'Maquina': m,
                            'Producto': p,
                            'Prioridad': pr,
                            'Cantidad': int(x[m,p,pr].value()),
                            'Tiempo_Total_Horas': round(tiempo_total, 2),
                            'Tasa_Produccion': tasa_produccion[m][p]
                        })
    
    df_plan = pd.DataFrame(resultados)
    
    # Crear DataFrames de resumen
    df_resumen_maquinas = df_plan.groupby('Maquina').agg({
        'Cantidad': 'sum',
        'Tiempo_Total_Horas': 'sum'
    }).round(2)
    
    df_utilizacion = pd.DataFrame({
        'Maquina': df_resumen_maquinas.index,
        'Utilizacion_Porcentaje': (df_resumen_maquinas['Tiempo_Total_Horas'] / 8 * 100).round(1)
    })
    
    df_prioridades = df_plan.groupby(['Producto', 'Prioridad']).agg({
        'Cantidad': 'sum',
        'Tiempo_Total_Horas': 'sum'
    }).round(2)
    
    df_productos = df_plan.groupby('Producto').agg({
        'Cantidad': 'sum',
        'Tiempo_Total_Horas': 'sum'
    }).round(2)
    
    return OptimizacionResultado(
        plan_produccion=df_plan,
        resumen_maquinas=df_resumen_maquinas,
        utilizacion_capacidad=df_utilizacion,
        resumen_prioridades=df_prioridades,
        resumen_productos=df_productos,
        tiempo_total=df_plan['Tiempo_Total_Horas'].sum(),
        status=status_msg
    )

def ejecutar_optimizacion(archivo_csv):
    """
    Ejecuta la optimización completa y retorna todos los DataFrames
    """
    try:
        demanda = procesar_ordenes(archivo_csv)
        resultados = optimizar_produccion(demanda)
        
        print("\n=== REPORTE DE OPTIMIZACIÓN ===")
        print("\nUtilización de máquinas:")
        print(resultados.utilizacion_capacidad.to_string(index=False))
        
        print("\nResumen por prioridad:")
        print(resultados.resumen_prioridades)
        
        return resultados
        
    except Exception as e:
        print(f"Error en la optimización: {str(e)}")
        return None

# Ejemplo de uso
if __name__ == "__main__":
    datos_csv = "./new_orders/orders.csv"
    
    resultados = ejecutar_optimizacion(datos_csv)

Welcome to the CBC MILP Solver 
Version: 2.10.3 
Build Date: Dec 15 2019 

command line - /home/silvestf/Documents/freudenberg/venv/lib/python3.10/site-packages/pulp/solverdir/cbc/linux/64/cbc /tmp/1a20e29dd2d84834bbb00e624dcfb06d-pulp.mps -timeMode elapsed -branch -printingOptions all -solution /tmp/1a20e29dd2d84834bbb00e624dcfb06d-pulp.sol (default strategy 1)
At line 2 NAME          MODEL
At line 3 ROWS
At line 31 COLUMNS
At line 180 RHS
At line 207 BOUNDS
At line 226 ENDATA
Problem MODEL has 26 rows, 20 columns and 110 elements
Coin0008I MODEL read with 0 errors
Option for timeMode changed from cpu to elapsed
Continuous objective value is 2.94219 - 0.00 seconds
Cgl0004I processed model has 21 rows, 19 columns (17 integer (0 of which binary)) and 90 elements
Cbc0012I Integer solution of 2.9501263 found by DiveCoefficient after 0 iterations and 0 nodes (0.00 seconds)
Cbc0038I Full problem 21 rows 19 columns, reduced to 17 rows 11 columns
Cbc0031I 3 added rows had average density of 1

KeyboardInterrupt: 

Cbc0010I After 50473000 nodes, 46191 on tree, 2.9441394 best solution, best possible 2.944098 (6658.36 seconds)
Cbc0010I After 50474000 nodes, 46152 on tree, 2.9441394 best solution, best possible 2.944098 (6658.49 seconds)
Cbc0010I After 50475000 nodes, 46107 on tree, 2.9441394 best solution, best possible 2.944098 (6658.61 seconds)
Cbc0010I After 50476000 nodes, 46067 on tree, 2.9441394 best solution, best possible 2.944098 (6658.74 seconds)
Cbc0010I After 50477000 nodes, 46078 on tree, 2.9441394 best solution, best possible 2.944098 (6658.86 seconds)
Cbc0010I After 50478000 nodes, 46008 on tree, 2.9441394 best solution, best possible 2.944098 (6658.99 seconds)
Cbc0010I After 50479000 nodes, 45952 on tree, 2.9441394 best solution, best possible 2.944098 (6659.16 seconds)
Cbc0010I After 50480000 nodes, 45906 on tree, 2.9441394 best solution, best possible 2.944098 (6659.28 seconds)
Cbc0010I After 50481000 nodes, 45881 on tree, 2.9441394 best solution, best possible 2.944098 (6659.40 s

In [14]:
plan_ordenado.groupby(['Maquina']).sum()

Producto  Prioridad  Cantidad  Tiempo_Total_Horas  Tasa_Produccion  \
Maquina                                                                      
M1            BB          3       362                2.99              242   
M2         BAAAB         11      1053                8.01              674   

         Hora_Inicio  Hora_Fin  
Maquina                         
M1                 0  2.991736  
M2                 0  7.998910

In [ ]:
plan_ordenado